In [19]:
import pandas as pd
import matplotlib
import matplotlib.pyplot as plt

In [20]:
#---------------------US Data
US_COVID_Cases = pd.read_csv("https://raw.githubusercontent.com/rmikula-gmu/cs504_test1_medium_tutorial/main/CS504%20Final%20Datasets%20Revised/US%20COVID%20Data.csv")
US_Stimulus = pd.read_csv("https://raw.githubusercontent.com/rmikula-gmu/cs504_test1_medium_tutorial/main/CS504%20Final%20Datasets%20Revised/DOL%20US%20Claims%20Data.csv")
US_Unemployment = pd.read_csv("https://raw.githubusercontent.com/rmikula-gmu/cs504_test1_medium_tutorial/main/CS504%20Final%20Datasets%20Revised/US%20Unemp%20Data.csv")
US_Master_data = pd.read_csv("https://raw.githubusercontent.com/rmikula-gmu/cs504_test1_medium_tutorial/main/CS504%20Final%20Datasets%20Revised/US%20Master%20Dataset.csv")
#---------------------Canada Data
Canada_COVID_Cases = pd.read_csv("https://raw.githubusercontent.com/rmikula-gmu/cs504_test1_medium_tutorial/main/CS504%20Final%20Datasets%20Revised/Canada%20COVID%20Data.csv")
Canada_Stimulus = pd.read_csv("https://raw.githubusercontent.com/rmikula-gmu/cs504_test1_medium_tutorial/main/CS504%20Final%20Datasets%20Revised/Canadian%20Recovery%20Benefit%20applications%20and%20total%20gross%20amount.csv")
Canada_Unemployment = pd.read_csv("https://raw.githubusercontent.com/rmikula-gmu/cs504_test1_medium_tutorial/main/CS504%20Final%20Datasets%20Revised/Canada%20Unemployment%20Data.csv")
Canada_Master_data = pd.read_csv("https://raw.githubusercontent.com/rmikula-gmu/cs504_test1_medium_tutorial/main/CS504%20Final%20Datasets%20Revised/Canada%20Master%20Data.csv")

In [21]:
US_Master_data.Date = US_Master_data.Date.str.strip()
Canada_Master_data.Date = Canada_Master_data.Date.str.strip()

US_Master_data['Date'] = pd.to_datetime(US_Master_data['Date'])
Canada_Master_data['Date'] = pd.to_datetime(Canada_Master_data['Date'])

In [22]:
US_Master_data['Initial Claims'] = US_Master_data['Initial Claims'].str.replace(',','')
US_Master_data['Monthly new case'] = US_Master_data['Monthly new case'].str.replace(',','')
US_Master_data['Civilian noninstitutional population'] = US_Master_data['Civilian noninstitutional population'].str.replace(',','')
US_Master_data['Employed Total'] = US_Master_data['Employed Total'].str.replace(',','')
US_Master_data['Unemployed Total'] = US_Master_data['Unemployed Total'].str.replace(',','')

In [23]:
US_Master_data['Initial Claims'] = US_Master_data['Initial Claims'].astype(int)
US_Master_data['Monthly new case'] = US_Master_data['Monthly new case'].astype(int)
US_Master_data['Civilian noninstitutional population'] = US_Master_data['Civilian noninstitutional population'].astype(int)
US_Master_data['Employed Total'] = US_Master_data['Employed Total'].astype(int)
US_Master_data['Unemployed Total'] = US_Master_data['Unemployed Total'].astype(int)
US_Master_data['Avg Insured Unemployment Rate'] = US_Master_data['Avg Insured Unemployment Rate'].astype(int)
US_Master_data['Avg Employed Percent of Population'] = US_Master_data['Avg Employed Percent of Population'].astype(int)
US_Master_data['Avg Percent of Population'] = US_Master_data['Avg Percent of Population'].astype(int)
US_Master_data['Avg Unemployed Percent of Labor Force'] = US_Master_data['Avg Unemployed Percent of Labor Force'].astype(int)

In [31]:
US_Master_data.head()

Date        Country       State  Initial Claims  \
0 2020-01-01  United States     Alabama           12819   
1 2020-01-01  United States      Alaska            4536   
2 2020-01-01  United States     Arizona           15413   
3 2020-01-01  United States    Arkansas            8481   
4 2020-01-01  United States  California          199167   

   Avg Insured Unemployment Rate  Monthly new case  \
0                              0                 0   
1                              3                 0   
2                              0                 1   
3                              1                 0   
4                              2                 0   

   Civilian noninstitutional population  Avg Employed Percent of Population  \
0                               3876526                                  56   
1                                546109                                  61   
2                               5802213                                  58   
3                               2353674                                  56   
4                              39118595                                  60   

   Employed Total  Avg Percent of Population  \
0         2180872                         57   
1          335692                         64   
2         3409624                         61   
3         1322159                         58   
4        23556224                         63   

   Avg Unemployed Percent of Labor Force  Unemployed Total  
0                                      2             59405  
1                                      5             17657  
2                                      4            171670  
3                                      3             50132  
4                                      4           1073820

In [24]:
from pycaret.classification import *

In [25]:
import numpy as np
from pandas_profiling import ProfileReport

In [26]:
profile = ProfileReport(US_Master_data, title="US Master Data")
profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [27]:
profile.to_file("US_Master_Data.html")

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [28]:
US_Master_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1071 entries, 0 to 1070
Data columns (total 12 columns):
 #   Column                                 Non-Null Count  Dtype         
---  ------                                 --------------  -----         
 0   Date                                   1071 non-null   datetime64[ns]
 1   Country                                1071 non-null   object        
 2   State                                  1071 non-null   object        
 3   Initial Claims                         1071 non-null   int64         
 4   Avg Insured Unemployment Rate          1071 non-null   int64         
 5   Monthly new case                       1071 non-null   int64         
 6   Civilian noninstitutional population   1071 non-null   int64         
 7   Avg Employed Percent of Population     1071 non-null   int64         
 8   Employed Total                         1071 non-null   int64         
 9   Avg Percent of Population              1071 non-null   int64   

In [29]:
data = US_Master_data.sample(frac=0.9, random_state=786).reset_index(drop=True)
data_unseen = US_Master_data.drop(data.index).reset_index(drop=True)

print('Data for Modeling: ' + str(data.shape))
print('Unseen Data For Predictions: ' + str(data_unseen.shape))

Data for Modeling: (964, 12)
Unseen Data For Predictions: (107, 12)


In [30]:
from pycaret.regression import *

In [32]:
exp_reg101 = setup(data = data, target = 'Initial Claims', session_id=123) 

In [33]:
compare_models()

RandomForestRegressor(bootstrap=True, ccp_alpha=0.0, criterion='mse',
                      max_depth=None, max_features='auto', max_leaf_nodes=None,
                      max_samples=None, min_impurity_decrease=0.0,
                      min_impurity_split=None, min_samples_leaf=1,
                      min_samples_split=2, min_weight_fraction_leaf=0.0,
                      n_estimators=100, n_jobs=-1, oob_score=False,
                      random_state=123, verbose=0, warm_start=False)

In [34]:
ada = create_model('ada')

In [35]:
print(ada)

AdaBoostRegressor(base_estimator=None, learning_rate=1.0, loss='linear',
                  n_estimators=50, random_state=123)


In [36]:
lightgbm = create_model('lightgbm')

In [37]:
dt = create_model('dt')

In [38]:
tuned_ada = tune_model(ada)

In [39]:
print(tuned_ada)

AdaBoostRegressor(base_estimator=None, learning_rate=1e-07, loss='square',
                  n_estimators=180, random_state=123)


In [40]:
tuned_lightgbm = tune_model(lightgbm)

In [41]:
tuned_dt = tune_model(dt)

In [42]:
plot_model(tuned_lightgbm)

In [43]:
plot_model(tuned_lightgbm, plot = 'error')

In [44]:
plot_model(tuned_lightgbm, plot='feature')

In [45]:
evaluate_model(tuned_lightgbm)

interactive(children=(ToggleButtons(description='Plot Type:', icons=('',), options=(('Hyperparameters', 'param…

In [46]:
predict_model(tuned_lightgbm);

In [48]:
final_lightgbm = finalize_model(tuned_lightgbm)

[LightGBM] [Warning] bagging_fraction is set=0.9, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9
[LightGBM] [Warning] feature_fraction is set=0.5, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.5
[LightGBM] [Warning] bagging_freq is set=3, subsample_freq=0 will be ignored. Current value: bagging_freq=3
[LightGBM] [Warning] bagging_fraction is set=0.9, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9
[LightGBM] [Warning] feature_fraction is set=0.5, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.5
[LightGBM] [Warning] bagging_freq is set=3, subsample_freq=0 will be ignored. Current value: bagging_freq=3
[LightGBM] [Warning] bagging_fraction is set=0.9, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9
[LightGBM] [Warning] feature_fraction is set=0.5, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.5
[LightGBM] [Warning] bagging_freq is set=3, subsample_freq=0 

In [49]:
print(final_lightgbm)

LGBMRegressor(bagging_fraction=0.9, bagging_freq=3, boosting_type='gbdt',
              class_weight=None, colsample_bytree=1.0, feature_fraction=0.5,
              importance_type='split', learning_rate=0.4, max_depth=-1,
              min_child_samples=6, min_child_weight=0.001, min_split_gain=0.3,
              n_estimators=20, n_jobs=-1, num_leaves=150, objective=None,
              random_state=123, reg_alpha=0.005, reg_lambda=0.0005,
              silent='warn', subsample=1.0, subsample_for_bin=200000,
              subsample_freq=0)


In [50]:
unseen_predictions = predict_model(final_lightgbm, data=data_unseen)
unseen_predictions.head()

Date        Country          State  Initial Claims  \
0 2021-07-01  United States       Virginia           31288   
1 2021-07-01  United States     Washington           27091   
2 2021-07-01  United States  West Virginia            4869   
3 2021-07-01  United States      Wisconsin           37887   
4 2021-07-01  United States        Wyoming            1675   

   Avg Insured Unemployment Rate  Monthly new case  \
0                              0             16302   
1                              2             23551   
2                              1              3196   
3                              1             10271   
4                              0              2949   

   Civilian noninstitutional population  Avg Employed Percent of Population  \
0                               6752073                                  60   
1                               6168817                                  60   
2                               1436659                                  52   
3                               4672898                                  63   
4                                457723                                  61   

   Employed Total  Avg Percent of Population  \
0         4065578                         62   
1         3707080                         63   
2          753130                         55   
3         2982792                         66   
4          280242                         64   

   Avg Unemployed Percent of Labor Force  Unemployed Total         Label  
0                                      4            176193  32540.129549  
1                                      5            199207  26291.467439  
2                                      5             39933   -292.727983  
3                                      3            121562  33250.421183  
4                                      5             15430    359.378588